In [1]:
# Load symbolicregression model

import torch
import os, sys
import symbolicregression
import sympytorch
import requests
from sympy.core.rules import Transform

model_path = "ckpt/model.pt" 
try:
    if not os.path.isfile(model_path): 
        print("Downloading model...")
        url = "https://dl.fbaipublicfiles.com/symbolicregression/model1.pt"
        r = requests.get(url, allow_redirects=True)
        open(model_path, 'wb').write(r.content)
    if not torch.cuda.is_available():
        sr_model = torch.load(model_path, map_location=torch.device('cpu'))
    else:
        sr_model = torch.load(model_path)
        sr_model = sr_model.cuda()
    print(sr_model.device)
    print("Model successfully loaded!")

except Exception as e:
    print("ERROR: model not loaded! path was: {}".format(model_path))
    print(e)    
    
est = symbolicregression.model.SymbolicTransformerRegressor(
                        model=sr_model,
                        max_input_points=10001,
                        n_trees_to_refine=5,
                        rescale=True
                        )

cuda:0
Model successfully loaded!


In [2]:
#sr_model.env.equation_id2word

In [2]:
# from transformers import AutoTokenizer
# CONTEXT_LENGTH = 256
# tokenizer = AutoTokenizer.from_pretrained("xhyi/PT_GPTNEO350_ATG") 
# tokenizer.pad_token = tokenizer.eos_token
# from transformers import AutoModelForCausalLM, TrainingArguments, Trainer
# model = AutoModelForCausalLM.from_pretrained("datasets/normalize_symbolic_regression_results_20231215/gptneo-350m-5500.model")


from transformers import T5Tokenizer, DataCollatorForSeq2Seq
from transformers import T5ForConditionalGeneration, Seq2SeqTrainingArguments, Seq2SeqTrainer

# Load the tokenizer, model, and data collator
MODEL_NAME = "google/flan-t5-base"

tokenizer = T5Tokenizer.from_pretrained(MODEL_NAME)
model = T5ForConditionalGeneration.from_pretrained("datasets/normalize_symbolic_regression_results_flant5_20231219/flant5-base-36000-loss0.097.model")
data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model)

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thouroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [3]:
import numpy as np
import sympy as sp
from sympy import sympify, lambdify, symbols, integrate, Interval, Symbol, I, S, oo, plot
from IPython.display import display

# Given an expr f (of variable t), returns its integral, together with t's and y's for regression
def integrate_expr(f, min_x=-4.0, max_x=4.0, increment=0.002, verbose=False):
    if verbose:
        print("Running integration on")
        display(f)
    # Compute integration
    x, t = symbols(['x','t'])
    fi = integrate(f, t)
    if verbose:
        display(fi)
        #plot(fi, (t, min_x, max_x))
    # Generate data for symbolic regression
    fl = lambdify((t), fi, "numpy")
    ts = np.arange(min_x, max_x, increment)
    ys = fl(ts)
    return fi, ts, ys
    
integrate_expr(sympify("2*t**2-t*2+2.5"), verbose=True)

Running integration on


2*t**2 - 2*t + 2.5

0.666666666666667*t**3 - 1.0*t**2 + 2.5*t

(0.666666666666667*t**3 - 1.0*t**2 + 2.5*t,
 array([-4.   , -3.998, -3.996, ...,  3.994,  3.996,  3.998]),
 array([-68.66666667, -68.58170266, -68.49681062, ...,  36.50791852,
         36.56077862,  36.61369466]))

In [4]:
from utils.utils import *

def round_expr(expr, num_digits=2):
    return expr.xreplace(Transform(lambda x: x.round(num_digits), lambda x: isinstance(x, sp.Float)))

# Run symbolic regression on given data
# Returns: (raw regressed expr, rounded expr, model refined expr)
@timeout(15)
def symbolic_regress(sr_model, xs, ys, generate_refinement=True, verbose=False):
    if verbose:
        print("Running Symbolic Regression...")
    ##Example of data
    xs = np.reshape(xs, (len(xs),1))
    ys = np.reshape(ys, (len(ys),1))
    sr_model.fit(xs,ys)
    #
    replace_ops = {"add": "+", "mul": "*", "sub": "-", "pow": "**", "inv": "1/"}
    model_str = sr_model.retrieve_tree(with_infos=True)["relabed_predicted_tree"].infix()
    for op,replace_op in replace_ops.items():
        model_str = model_str.replace(op,replace_op)
    #
    raw_expr = sp.parse_expr(model_str)
    x_0, t = symbols(['x_0', 't'])
    raw_expr = raw_expr.subs(x_0, t)
    if verbose:
        display(raw_expr)
    #
    expr = sp.expand(raw_expr)
    rounded_expr = round_expr(expr)
    if verbose:
        display(rounded_expr)
    #
    # Encode some input text
    if generate_refinement:
        prompt = str(rounded_expr)
        input_ids = tokenizer.encode(prompt, return_tensors='pt')
        #
        # Generate text
        output = model.generate(input_ids, max_length=50, num_return_sequences=1, temperature=0.1)
        #
        # Decode and print the output
        generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
        generated_expr = sympify(generated_text)
        if verbose:
            display(generated_expr)
        #
    else:
        generated_expr = None
    return raw_expr, rounded_expr, generated_expr


fi, ts, ys = integrate_expr(sympify("2*t**2-t*2+2.5"), verbose=False)
rounded_fi = round_expr(fi)
display(rounded_fi)
raw_expr, rounded_expr, generated_expr = symbolic_regress(est, ts, ys, verbose=False)
display(generated_expr)

print("Diff1:")
display(rounded_fi-rounded_expr)
print("Diff2:")
display(rounded_fi-generated_expr)

0.67*t**3 - 1.0*t**2 + 2.5*t

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(


0.67*t**3 - t**2 + 2.5*t

Diff1:


0

Diff2:


-7.812500000004e-5*t**3

In [5]:
# import json
# import random
# import numpy as np

# def load_expressions(filepaths):
#     lines = []
#     for filepath in filepaths:
#         fin = open(filepath, 'r')
#         lines.extend(fin.readlines())
#         fin.close()
#     #
#     random.shuffle(lines)
#     exprs = set()
#     for line in lines:
#         data = json.loads(line)
#         for k,v in data.items():
#             if k in ('f_t', 'g_t'):
#                 try:
#                     if 'sqrt' not in v[1]:
#                         expr = sympify(v[1])
#                         exprs.add(expr)
#                 except:
#                     continue
#     return exprs

# exprs = load_expressions(['datasets/parametric_equations.json'])  #'datasets/function_evaluation.json', 

In [6]:
# # Run symbolic regression on each case

# seen_exprs = set()
# # fin = open("datasets/parametric_equations_polynomial_integral_results.json", "r")
# # lines = fin.readlines()
# # for line in lines:
# #     result = json.loads(line)
# #     expr = result["original"]
# #     seen_exprs.add(expr)
# # fin.close()
# # print(f"{len(seen_exprs)} exprs loaded")

# fout = open("datasets/parametric_equations_polynomial_integral_results.json", "a")
# num_seen = 0
# num_seen_changed = False

# for f in exprs:
#     if str(f) in seen_exprs:
#         num_seen+=1
#         num_seen_changed = True
#         continue
#     else:
#         num_seen_changed = False
#     if num_seen_changed:
#         print(f"{num_seen} exprs ignored")
#     #print("Original expr and its integral:")
#     #display(f)
#     #print(f)
#     try:
#         fi, xs, ys = integrate_expr(f, verbose=False)
#         x, t = symbols(['x','t'])
#         fi = fi.subs({x:t})
#         rounded_fi = round_expr(fi)
#         #display(rounded_fi)
#         raw_expr, rounded_expr, generated_expr = symbolic_regress(est, xs, ys, generate_refinement=True, verbose=False)
# #         print("Generated expr:")
# #         display(generated_expr)
#         results = {"original":str(f),
#                    "integral":str(fi),
#                    "rounded_integral":str(rounded_fi),
#                    "regressed":str(raw_expr),
#                    "rounded_regressed":str(rounded_expr),
#                    "generated_regressed":str(generated_expr),
#                    "diff_rounded": str(rounded_fi-rounded_expr),
#                    "diff_generated": str(rounded_fi-generated_expr)
#                   }
#         fout.write(json.dumps(results))
#         fout.write('\n')
#         fout.flush()
#     except:
#         print("Failed to run symbolic regression")
#         continue
#     #     print("Diff1:")
#     #     display(rounded_fi-rounded_expr)
#     #     print("Diff2:")
#     #     display(rounded_fi-generated_expr)

# fout.close()

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

...

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the fi

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(


In [7]:
# Check the accuracy of symbolic regression

import json
from sympy import evalf, N
from utils.utils import *


# Check if f1 and f2 are almost equal.
# Note: Relative error is defined based on f1. Please use the original expression as f1.
def almost_equal(f1, f2, max_abs_error=0.011, max_relative_error=0.011, verbose=False):
    expr = f1-f2
    coeff_pairs = None
    try:
        coeff_pairs = get_coefficients_and_exponents(expr)
    except:
        print("Cannot get_coefficients_and_exponents")
        print(str(expr))
    if coeff_pairs is None:
        constants = get_all_constants(expr)
    else:
        constants = [p[0] for p in coeff_pairs]
    # Check if all diffs are within max_abs_error
    violators = [c for c in constants if c == sp.nan or abs(c) > max_abs_error]
    if verbose:
        print("Violating constants:", violators)
    if len(violators) == 0:
        return True
    # Check if all violating diffs are within max_relative_error
    try:
        coeffs1 = get_polynomial_coeffs(f1)
        coeffs2 = get_polynomial_coeffs(f2)
    except:
        return False
    for i in range(len(coeffs1)):
        if abs(coeffs1[i] - coeffs2[i]) > max_abs_error and \
           abs(coeffs1[i] - coeffs2[i]) > max_relative_error*abs(coeffs1[i]):
            return False
    return True
    

# fin = open("datasets/parametric_equations_polynomial_integral_results.json", "r")
# lines = fin.readlines()

# num_total, qualified_rounded, qualified_generated = 0, 0, 0
# for line in lines:
#     result = json.loads(line)
#     if "diff_rounded" not in result or "diff_generated" not in result:
#         continue
#     rounded_integral = N(sympify(result["rounded_integral"]))
#     rounded_regressed = N(sympify(result["rounded_regressed"]))
# #     display(rounded_integral)
# #     display(rounded_regressed)
#     try:
#         rounded_regressed = filter_non_polynomial(rounded_regressed)
#     except:
#         print("Cannot filter non-polynomials on", str(rounded_regressed))
#     #generated_regressed = N(sympify(result["generated_regressed"]))
#     diff_rounded = rounded_integral - rounded_regressed
#     #diff_generated = sympify(result["diff_generated"])
#     num_total += 1
#     if almost_equal(rounded_integral, rounded_regressed, verbose=False):
#         qualified_rounded += 1
#     else:
#         display(rounded_integral)
#         display(rounded_regressed)
#         print(rounded_regressed)
#         display(diff_rounded)
# #     if is_close_to_zero(diff_generated, True):
# #         qualified_generated += 1
    
# fin.close()

# print(num_total, qualified_rounded, qualified_generated)

4.25*t**2 + 3.25*t

4.25*t**2 + 3.25*t

Violating constants: []


2.17*t**2 - 8.67*t

2.17*t**2 - 8.67*t

...

Violating constants: []


1.86*t**2 + 8.71*t

1.86*t**2 + 8.71*t

Violating constants: []



KeyboardInterrupt



In [8]:
# Get the diff (as a 1-D numpy array) between two functions f and g
def get_diff(f, g, t, min_t=-5.0, max_t=5.0, increment=0.1):
    ts = np.arange(min_t, max_t, increment)
    fl = lambdify((t), f, "numpy")
    fs = fl(ts)
    gl = lambdify((t), g, "numpy")
    gs = gl(ts)
    return fs, gs, fs-gs

def get_avg_diff(f, g, t, min_t=-5.0, max_t=5.0, increment=0.1):
    fs, gs, diff = get_diff(f, g, t, min_t, max_t, increment)
    avg_f = np.mean(np.abs(fs))
    avg_g = np.mean(np.abs(gs))
    avg_diff = np.mean(np.abs(diff))
    return avg_diff / max(avg_f, avg_g)

# for i in range(1000):
#     f = originals[i]
#     x, t = symbols(['x','t'])
#     fi = integrate(f, t)
#     g = integrals[i]
#     #fs, gs, diff = get_diff(fi, g, t)
#     # print(np.mean(np.abs(fs)))
#     # print(np.mean(np.abs(gs)))
#     # print(np.mean(np.abs(diff)))
#     relative_diff = get_avg_diff(fi, g, t)
#     if relative_diff > 0.01:
#         print("CASE", i)
#         display(fi)
#         display(g)
#         print(relative_diff)

In [9]:
# Generate data for regression to infer the rules for integral
# The data is in the following format:
# Let us suppose there are N regression problems, and MAX_POWER=6, which is 
#   the highest power allowed in our polynomials.
#   data_series is a list of 7 items, each corresponding to a particular power
#   Each item is a tuple of 2 elements, with the first being x's and the second
#   being y's for the regression problem for the corresponding power.
#   The y's is a 1-D array of size N, which is the coefficient of that particular power for
#   each of N regression problems.
#   The each of the x's is an array of size 14, which contains 
#   [0, coeff-power-0, 1, coeff-power-1, 2, coeff-power-2, ...]
# If we want to find the connection between x's and y's, we should find that
#   y_1 = x_1 (coeff-power-0)
#   y_2 = x_3 (coeff-power-1)
#   y_3 = x_5 (coeff-power-2)
#   y_4 = x_7 (coeff-power-3)
#   y_5 = x_9 (coeff-power-4)

from sympy import evalf, N
from utils.utils import *

fin = open("datasets/parametric_equations_integral_results.json", "r")
lines = fin.readlines()

MAX_POWER = 6
MAX_AVG_DIFF = 0.01

data_series = [([],[])] * (MAX_POWER+1)
data_series = []
originals = []
integrals = []
t = Symbol('t')

for i in range(MAX_POWER+1):
    data_series.append((list(),list()))

for line in lines:
    result = json.loads(line)
    if "rounded_regressed" not in result:
        continue
    original = N(sympify(result["original"]))
    integral = N(sympify(result["rounded_regressed"]))
    try:
        original = filter_non_polynomial(original)
        integral = filter_non_polynomial(integral)
        original_integral = integrate(original, t)
        avg_diff = get_avg_diff(original_integral, integral, t)
        if avg_diff > MAX_AVG_DIFF:
            print("Skipping due to diff=", avg_diff)
            display(original_integral)
            display(integral)
            continue
    except:
        print("Cannot filter non-polynomials on", str(integral))
        continue
    try:
        coeffs_original = get_polynomial_coeffs(original)
        coeffs_integral = get_polynomial_coeffs(integral)
    except:
        print("Cannot get_coefficients_and_exponents")
        display(integral)
        continue
    if original.is_constant():
        print("Skipping", line)
        continue
    xs = list()
    for i in range(MAX_POWER+1):
        xs.append(i)
        xs.append(coeffs_original[i])
    for i in range(MAX_POWER+1):
        data_series[i][0].append(xs.copy())
        data_series[i][1].append(coeffs_integral[i])
    if len(data_series[0][1]) % 100 == 0:
        print(len(data_series[0][1]), "processed")
#     if len(data_series[0][1]) == 3844:
#         display(original)
#         print(original.is_constant())
#         display(sympify(result["original"]))
#         display(integral)
    originals.append(original)
    integrals.append(integral)
    
fin.close()


Skipping due to diff= 0.015716668729117315


0.0533333333333333*t**3 - 0.48*t**2 + 1.44*t

0.05*t**3 - 0.48*t**2 + 1.45*t + 0.01

Skipping due to diff= 0.027144128911185422


4.33333333333333*t**2 - 0.333333333333333*t

...

0.02*t**3 + 2.18*t**2 + 73.19*t

Skipping due to diff= 1.002888134107593


-3.5*t**2 - 4.6*t

0.01*t**2 + 0.02*t

8800 processed


In [10]:
import pickle

# fout = open('/tmp/test_data_series.pkl', 'wb')
# pickle.dump(data_series, fout)
# fout.close()

fin = open('/tmp/test_data_series.pkl', 'rb')
data_series = pickle.load(fin)
fin.close()

# Check if the results are as expected
n = len(data_series[1][1])
for y_idx in range(3, 4):
    xs = np.asarray(data_series[y_idx][0])
    x1s = xs[:,(y_idx-1)*2+1]
    ys = data_series[y_idx][1]
    for i in range(n):
        if abs(ys[i] - x1s[i]/y_idx) > 0.02 and abs(ys[i]/(x1s[i]/y_idx)-1) > 0.02:
            print(f"y_idx={y_idx}, i={i}, x={x1s[i]}, y={ys[i]}")
            display(originals[i])
            display(integrals[i])

y_idx=3, i=10, x=0.3333333333333333, y=0.08


0.333333333333333*t**2 + 10.6666666666667*t + 85.3333333333333

0.08*t**3 + 5.35*t**2 + 86.04*t

y_idx=3, i=62, x=0.3333333333333333, y=0.0


0.333333333333333*t**2 + 17.3333333333333*t + 225.333333333333

...

0.0625*t**2 + 4.125*t + 68.0625

2.08*t**2 + 68.27*t

y_idx=3, i=8330, x=0.16, y=0.0


0.16*t**2 + 7.04*t + 77.44

3.49*t**2 + 78.04*t

In [18]:
y_idx=1

n = len(data_series[1][1])

est_simple = symbolicregression.model.SymbolicTransformerRegressor(
                        model=sr_model,
                        max_input_points=10001,
                        n_trees_to_refine=100,
                        rescale=True
                        )


xs = np.asarray(data_series[y_idx][0])
x1s = np.reshape(xs[:,y_idx], (n,1))
ys = np.reshape(data_series[y_idx][1], (n,1))
ys = ys + 2*x1s*x1s + 3.5

print(xs[0:10, y_idx])
print(ys[0:10])

est_simple.fit(x1s,ys)

replace_ops = {"add": "+", "mul": "*", "sub": "-", "pow": "**", "inv": "1/"}
model_str = est_simple.retrieve_tree(with_infos=True)["relabed_predicted_tree"].infix()
for op,replace_op in replace_ops.items():
    model_str = model_str.replace(op,replace_op)
    
print(model_str)

raw_expr = sp.parse_expr(model_str)
sp.simplify(sp.expand(round_expr(raw_expr)))

[16.      1.      5.75   45.5625 64.      2.25   -2.5    -1.25   -5.
 -3.25  ]
[[5.31610000e+02]
 [6.50000000e+00]
 [7.53750000e+01]
 [4.20094281e+03]
 [8.25950000e+03]
 [1.58750000e+01]
 [1.35000000e+01]
 [5.37500000e+00]
 [4.85000000e+01]
 [2.13750000e+01]]


/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

((74.43759358029932 + (56.785347440652785 * (((0.34115272275857256 + (0.7878761293599857 * (-0.4280303776973979 + (0.019889758680590723 * x_0)))) * (11.97586863901531 + (5.909402626581631e-06 * (((-8.364307878543212 + (0.9869113121530284 * (-0.4280303776973979 + (0.019889758680590723 * x_0)))) * (0.3716268090946336 + (0.10196054868766333 * (-0.4280303776973979 + (0.019889758680590723 * x_0))))))**2))))**2)) - (71.06240641969787 + (-0.012295749715040253 * (((0.40499982411304064 + (0.013997598128293666 * (-0.4280303776973979 + (0.019889758680590723 * x_0)))) * (0.006502676229051508 + (0.013995963101457603 * (-0.4280303776973979 + (0.019889758680590723 * x_0))))))**2)))


2.0*x_0**2 + 1.0*x_0 + 3.5048828125

In [22]:
y_idx=2
n = len(data_series[1][1])

xs = np.asarray(data_series[y_idx][0])
x3s = np.reshape(xs[:,2*y_idx+1], (n,1))
ys = np.reshape(data_series[y_idx][1], (n,1))
ys = ys + 2*x3s*x3s + 3.5

# print(xs[0:10, 1])
# print(ys[0:10])

est_simple.fit(x3s,ys)

replace_ops = {"add": "+", "mul": "*", "sub": "-", "pow": "**", "inv": "1/"}
model_str = est_simple.retrieve_tree(with_infos=True)["relabed_predicted_tree"].infix()
for op,replace_op in replace_ops.items():
    model_str = model_str.replace(op,replace_op)
    
print(model_str)

raw_expr = sp.parse_expr(model_str)
sp.simplify(sp.expand(round_expr(raw_expr)))

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/sklearn/metrics/_regression.py:478: RuntimeWarning: overflow encountered in square
  output_errors = np.average((y_true - y_pred) ** 2, axis=0, weights=sample_weight)
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a 

((-91.73548994203531 + (6.85543989417847 * (((10.130257747638987 + (-7.3145055409503374 * (-0.6085491829353974 + (0.04605635689950794 * x_0)))) - ((-1.0223618468695557 + (-24.014560908612186 * (-0.6085491829353974 + (0.04605635689950794 * x_0)))) + ((-4.790784415338443 + (-0.16404213381080984 * (-0.6085491829353974 + (0.04605635689950794 * x_0)))) * ((-0.2477958069911364 + (-0.8342933196106165 * (-0.6085491829353974 + (0.04605635689950794 * x_0)))) - (0.7808032091454022 + (2.297192733414792 * (-0.6085491829353974 + (0.04605635689950794 * x_0)))))))))**2)) - (91.00338156066384 + (-19.44674571772703 * ((-3.6940562737157565 + (-7.117921009823899 * (-0.6085491829353974 + (0.04605635689950794 * x_0)))))**2)))


/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/sklearn/metrics/_regression.py:1005: RuntimeWarning: overflow encountered in square
  numerator = (weight * (y_true - y_pred) ** 2).sum(axis=0, dtype=np.float64)


1.28e-5*x_0**4 - 0.00228*x_0**3 + 2.05*x_0**2 + 0.5*x_0 + 4.8479

In [40]:
import scipy

y_idx=2
ys = np.asarray(data_series[y_idx][1])
xs = np.asarray(data_series[y_idx][0])[:,3]

print(scipy.stats.linregress(xs, ys))

diff = (ys-xs/2).flatten()
for i in range(len(diff)):
    if abs(diff[i]) > 0.02:
        print(i, diff[i])

LinregressResult(slope=0.499996051853643, intercept=-0.00017935818398610165, rvalue=0.9999999442447394, pvalue=0.0, stderr=1.776822988022147e-06, intercept_stderr=8.73374665940944e-05)
31 -0.026666666666666394
62 0.053333333333334565
402 0.0344444444444445
431 -0.03000000000000025
679 0.040000000000000036
854 -0.040000000000000036
888 0.020000000000003126
937 -0.023333333333333428
942 -0.28999999999999915
1028 -0.10714285714285765
1103 0.030000000000000027
1121 -0.03000000000000025
1165 0.07888888888888879
1175 -0.060000000000002274
1205 -0.09999999999999964
1215 -0.04816326530612258
1230 -0.1999999999999993
1237 -0.13666666666666671
1402 -0.040000000000000036
1459 -0.13999999999999968
1606 0.04999999999999982
1647 0.021020408163265225
1841 -0.040000000000000036
1897 -0.11999999999999744
1978 0.040000000000000036
1986 0.03288395276380829
2038 0.04999999999999716
2132 0.09999999999999964
2173 0.040000000000000036
2295 -0.16000000000000014
2452 0.029999999999999805
2471 -0.17999999999999

In [35]:
print(ys.shape)
print(np.asarray(data_series[y_idx][0]).shape)

(8832,)
(8832, 14)
